In [1]:
import os
import json
import math
import torch
import numpy as np
import pandas as pd
from helper import draw
from WTDataset import WTDataset
from collections import Counter
from PIL import Image, ImageDraw
import plotly.graph_objects as go

In [2]:
# Open JSON data file
root = 'data/NordTank586x371'
f = open(os.path.join(root, "augment_json.json"))
data_dict = json.load(f)

In [3]:
# Check if all images have the same width and height
w, h = [], []
images = data_dict['images']
for img in images:
    w.append(img['width'])
    h.append(img['height'])

In [4]:
# All images have shape (586, 371)
print(Counter(h))
print(Counter(w))

Counter({371: 7170})
Counter({586: 7170})


In [5]:
# Number of labeled images vs unlabeled images
print("Total number of images:", len(images))
print("Total number of labeled images:", len(data_dict['annotations']))

Total number of images: 7170
Total number of labeled images: 7170


In [6]:
# Compute the amount of dirt and damage bounding boxes per image
dirt_img, damage_img = 0, 0
dirt, damage = [], []
annotations = data_dict['annotations']

for annotation in annotations:
    labels = annotation['labels']
    
    num_damage = labels.count(1.0)
    if num_damage != 0:
        damage_img += 1
    damage.append(num_damage)
    
    num_dirt = labels.count(2.0)
    if num_dirt != 0:
        dirt_img += 1
    dirt.append(num_dirt)


In [7]:
print("The number of images containing dirt annotations:", dirt_img)
print("The number of images containing damage annotations:", damage_img)
print("The number of dirt annotations:", sum(dirt))
print("The number of damage annotations:", sum(damage))

the number of images containing dirt annotations: 4738
the number of images containing damage annotations: 2527
the number of dirt annotations: 4889
the number of damage annotations: 8770


In [8]:
# Plot the amount of dirt and damage labels
fig = go.Figure(data=[go.Bar(x=['Dirt', 'Damage'], y=[sum(dirt), sum(damage)], marker_color='#AA0DFE')])
fig.update_layout(
    title_text='Count dirt and damage labels',
    yaxis_title_text='Count'
)
fig.show()

In [9]:
# Plot the amount of images containing dirt and/or damage annotations
fig = go.Figure(data=[go.Bar(x=['Dirt', 'Damage'], y=[dirt_img, damage_img], marker_color='#AA0DFE')])
fig.update_layout(
    title_text='Count images containing dirt/damage annotations',
    yaxis_title_text='Count'
)
fig.show()

In [10]:
# Plot the amount of dirt and damage bounding boxes per image (for annotated images)
fig = go.Figure()
fig.add_trace(go.Histogram(x=damage, name="Damage", marker_color='#DEA0FD'))
fig.add_trace(go.Histogram(x=dirt, name="Dirt", marker_color='#AA0DFE'))

fig.update_layout(
    title_text='Number of bounding boxes per image',
    xaxis_title_text='Number of bounding boxes',
    yaxis_title_text='Count',
    bargap=0.2,
    bargroupgap=0.1
)

fig.show()

In [11]:
# Compute the aspect ratios of the bounding boxes
ars, labels = [], []
annotations = data_dict['annotations']
for annotation in annotations:
    boxes = np.asarray(annotation['bboxes'], dtype=np.float32)
    ar = 1.0 * (np.abs(boxes[:, 0] - boxes[:, 2]) / np.abs(boxes[:, 1] - boxes[:, 3]))
    ars += list(ar)

In [12]:
# Plot the aspect ratios of the bounding boxes
fig = go.Figure(data=[go.Histogram(x=ars, marker_color='#AA0DFE')])

fig.update_layout(
    title_text='The aspect ratios of the bounding boxes',
    xaxis_title_text='Number of bounding boxes',
    yaxis_title_text='Count',
    bargap=0.2,
    bargroupgap=0.1
)

fig.show()

In [13]:
# Create a heatmap of all bounding box locations in the images
heatmap_dirt = np.zeros((371, 586), dtype=int)
heatmap_damage = np.zeros((371, 586), dtype=int)
for annotation in annotations:
    boxes = np.asarray(annotation['bboxes'], dtype=np.float32)
    if boxes.shape[1] != 0:
        for i, box in enumerate(boxes):
            l, r, t, b = draw(box, (586, 371))

            # Make separate heatmap for dirt and damage bounding boxes
            if annotation['labels'][i] == 1.0:
                heatmap_damage[int(t):int(b), int(l):int(r)] += 1
            else:
                heatmap_dirt[int(t):int(b), int(l):int(r)] += 1

In [14]:
# Plot heatmap of damage labeled bounding boxes
fig = go.Figure(data=go.Heatmap(
                    z=heatmap_damage))
fig.update_layout(
    title_text='Heatmap of the locations of the bounding boxes for damage'
)
fig['layout']['yaxis']['autorange'] = "reversed"
fig.show()

In [15]:
# Plot heatmap of dirt labeled bounding boxes
fig = go.Figure(data=go.Heatmap(
                    z=heatmap_dirt))
fig.update_layout(
    title_text='Heatmap of the locations of the bounding boxes for dirt'
)
fig['layout']['yaxis']['autorange'] = "reversed"
fig.show()